In [1]:
import pandas as pd
from google.cloud import bigquery
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import normalize
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from google.oauth2 import service_account
credentials = service_account.Credentials.from_service_account_file('/dbfs/FileStore/tables/My_First_Project_fe78171bdba0-bdf8d.json')
import pandas_gbq
pandas_gbq.context.credentials = credentials
from pyspark.sql.types import DoubleType, IntegerType, StringType, StructType, StructField

## Goals
This project will contain the following components:

* Web Scrape Indeed Job Listings
* Use Google BigQuery to Store Job and Skills Datasets
* Use TF-IDF for Content Recommendations with PySpark
* Determine cosine similarities for users and skills
* Return recommended jobs and skills for inputs

## Import Jobs Dataframe from Google BigQuery

My `Indeed Scraping Functions` R script performed webscraping of Indeed Job Postings for the following tech-related professions: 'Data+Scientist', 'Data+Analyst', 'Business+Analyst', 'Computer+Scientist', 'Software+Engineer', 'Systems+Analyst', 'Web+Developer', 'Database+Administrator', 'Programmer', 'SEO+Consultant', 'Digital+Marketing', 'UX+Designer', 'UI+Designer', 'Front+End+Developer', 'Data+Architect', 'Data+Engineer', 'Quality+Assurance+Analyst', 'Statistician', 'Software+Tester', 'Product+Analyst', 'IT+Support', 'Game+Developer', 'CRM+Analyst', 'Network+Engineer', 'Data+Modeler'. This script is available in the same Github repository as this notebook. 

After the webscraping was completed, the resulting dataframe was uploaded to a BigQuery datatable. In the code chunk below, I imported the job listings datatable as a pandas dataframe.

In [3]:
project_id='deep-rigging-245523'
query = "SELECT * FROM Projects.job_listings"
jobs_df = (pandas_gbq.read_gbq(query,project_id=project_id, dialect='standard')
           .drop_duplicates(subset = "description").fillna(''))
print(len(jobs_df))

2542

## Import Skills Dataframe from Google BigQuery

I also stored a list of LinkedIn skills in Google BigQuery, which is from this [Kaggle Dataset](https://www.kaggle.com/maneeshdisodia/employment-skills).

In [5]:
query = "SELECT * FROM Projects.skills"
skills_df = pandas_gbq.read_gbq(query,project_id=project_id, dialect='standard')
skills_df = skills_df.rename(columns={'string_field_0': 'name'})
print(len(skills_df))
display(skills_df.head(n=10))

name (ISC)2 .NET .NET CLR .NET Compact Framework .NET Framework .NET Remoting .Net Core .com .htaccess 1-4 Units

## Job Profile Inputs
To test the recommender system, the following user profiles are created. Each user profile has a list of skills associated with the profession. For example, I am a data analyst with skills in Python, R, SQL, Tableau, Power BI, Salesforce, Excel, Machine Learning, Statistics, Analytics, Visualization, Web Scraping, and BigQuery. This recommender system will suggest jobs and more useful skills for each user profile.

In [7]:
# input_profession = input("Enter your profession, or enter x to use default inputs ")
# if input_profession == "x":
user_profiles = [
  ("Data Analyst", ["Python", "R", "SQL", "Tableau", "Power BI", "Salesforce", "Excel",
                    "Machine Learning", "Statistics", "Analytics", "Visualization", "Web Scraping",
                    "Bigquery"]), # My profile
  ("Software Engineering", ["sql", "web apps", "react", "angular", "full stack", "javascript",
                            "node.js", "python", "AWS", "Java", "C++", "NOSQL", "Graph database",
                            "express", "Pyspark", "BigQuery", "S3", "serverless", "lambda"]),
  ("Data Engineer", ["MapReduce", "Hadoop", "Data mining", "ETL", "SPSS", "Java", "Scala", "SQL", "NOSQL", "cloudera"]),
  ("Web Developer", ["HTML", "CSS", "Javascript", "Ajax", "PHP", "ASP", "Java", "SEO", "SQL"]),
  ("UI UX Designer", ["Agile", "Prototyping", "Wireframing", "Design", "Data", "user research", "Business"]),
  ("Game developer", ["C++", "Visual Basic", "Java", "Autodesk Maya", "Physics", "Unity", "C#", "xcode", "photoshop", "autodesk 3dMax"])
]


The following code chunk converts all the user profiles to an individual string and removes duplicate words from the skills.

In [9]:
def remove_dups(ls):
  words = []
  for v in ls:
    for word in v.split():
      words.append(word)
  return list(set(words))
    
input_skills_strings = []
for input_profession, input_skills in user_profiles:
  input_skills_string = " ".join(remove_dups(input_skills + [input_profession]))
  input_skills_strings.append(input_skills_string)
input_skills_strings

Out[ 18 ]: 
['Machine Statistics Python Tableau Salesforce R Web Excel Analytics Bigquery BI Power Scraping Data Analyst Visualization SQL Learning',
 'NOSQL Pyspark Software Graph apps S3 C++ sql stack serverless AWS react Java express database node.js python full Engineering BigQuery angular javascript lambda web',
 'Hadoop NOSQL MapReduce SPSS Engineer Data mining Java ETL cloudera SQL Scala',
 'Developer Javascript Web Ajax SEO CSS PHP Java ASP HTML SQL',
 'UI Agile Design Data Business user Wireframing Designer Prototyping research UX',
 'Basic C++ photoshop 3dMax Physics Visual Game Autodesk xcode developer C# Java Unity autodesk Maya']

## Apply TF-IDF
The next step is to use TF-IDF with the full list of ~11,000 skills as the dictionary. The resulting dataframe `tfidf_jobs` has all the Indeed job listings and the six user profiles as rows and the skills as columns. The values represent the term frequency - inverse document frequency of each of the job-skill combinations.

In [11]:
# Import TfidfVectorizer
jobs_df["words"] = jobs_df["title"] + jobs_df["summary"] + jobs_df["description"]

# Create a TfidfVectorizer: tfidf
tfidf = TfidfVectorizer(stop_words="english", 
                        analyzer='word',
                        vocabulary = map(lambda x: str(x).lower(), skills_df.name.values),
                        ngram_range=(1, 3), max_df=0.1, min_df=0.0025, max_features=None)

# Apply fit_transform to job descriptions: tfidf_jobs
job_summaries = jobs_df["words"].astype(str).copy()
job_summaries = job_summaries.append(pd.Series(input_skills_strings))

tfidf_result = tfidf.fit_transform(job_summaries.values)

tfidf_jobs = pd.DataFrame(data = tfidf_result.toarray(), 
                          index = job_summaries, 
                          columns = tfidf.get_feature_names())

#normalize features
norm_features = normalize(tfidf_result.toarray())
jobs_rec_df = pd.DataFrame(norm_features, index = job_summaries, columns = tfidf.get_feature_names())

display(tfidf_jobs.tail())

(isc)2 .net .net clr .net compact framework .net framework .net remoting .net core .com .htaccess 1-4 units 1-wire 1-to-1 marketing 100% financing 100-105 100d 1031 exchanges 1099 preparation 10g ethernet 10k 10q 10b5-1 plans 10gr2 10gen 1120s 11781 11gr1 11gr2 123d catch 123d design 12c 12c release 2 144a 16pf 1709 18th century 1940 act 19th century 1h nmr 1password 1sync 1shoppingcart 2-d 2-d design 20-20 cap studio 20/20 design 20/20 design software 20/20 technologies 200-101 2008 r2 2012 r2 2013 (lync) 2014a 2015a 2016 r2 2017a 203k 20th century 21 cfr 21st century skills 220-801 220-802 220-901 220-902 24 hour emergency service 24x7 24x7 production support 27.x 2d animation 2d cad drawing 2d drawing 2d software 2d art 2d graphics 2d to 3d conversion 2do 2g 2v0 2nd line 2v0-641 2ε 340b 35mm 360 360 assessments 360 campaigns 360 degree assessment 360 feedback 360 recruitment 360s 365 37signals 3cx 3com nbx 3com switches 3d + animation 3d animation 3d architectural rendering 3d coat 3d design 3d drawing 3d gis 3d graphic design 3d graphics 3d home architect 3d mapping 3d materials 3d math 3d modeling 3d modeling software 3d packaging 3d particles and dynamics 3d printing 3d production 3d prototyping 3d reconstruction 3d rendering 3d scanning 3d secure 3d seismic interpretation 3d simulation 3d studio max 3d studio viz 3d textures 3d tracking 3d typography 3d visualization 3d and animation 3d displays 3d, animation & cao 3d, animation und cad 3d, animación y cad 3d-beleuchtung 3d-druck 3d-grafik 3d-materialien 3d-modellierung 3d-partikel und dynamik 3d-texturen 3dcom 3des 3dequalizer 3dtv 3dvia composer 3delight 3g 3gpp 3gpp2 3p 3par 3d 3ds max 3rd line support 3rd party integrations 3rd party liaison 3rd party partnerships 3rd party relationships 3rd party software integration 4 disciplines of execution 401(k) retirement savings plans 401k rollovers 403 b 404 compliance 409a 40g 457 plans 480interactive 49cfr 4g 4gl 4k 4pl 4th dimension 4x4 5 why 5.1 mixing 501c3 504 plans 529 plans 55+ communities 5500s 5d 5ess 5s 5y 60d 63 licenses 6502 assembly 650d 68hc11 68k 68k assembly 6d 6s 7 qc tools 700d 701 7d mark ii 8 wastes 8-d 802.11a 802.11b 802.11g 802.11i 802.11n 802.15.4 802.16e 802.1ag 802.1d 802.1q 802.1x 8051 assembly 8051 microcontroller 80x86 837i 837p 89c51 8d problem solving 960 grid system @task eclairage 3d eclairage et rendu eclairage photo equipement photo equipement video a + certified a&d a&e a&h a&p a&r administration a&u a+ a++ a-133 a-gps a-frames a/b testing a/r collections a/r management a/r analysis a1 assessor a10 a2 a2a a3 a3 thinking a320 a330 aaahc aacr2 aams aap aar aashto aaus scientific diver abap web dynpro abap-oo abb 800xa abbyy abbyy finereader abc analysis abc flowcharter abcp abel abi abls abo certified absynth abv ac drives ac nielsen ac/dc acad acars acats acbs acd acd management acdsee ace ace certified ace certified personal trainer acf2 acfe ach aci codes acis acls instruction acms acoa acord acp acpi acr acsa acsc acsls acsm acsm health fitness acsp acsr acss act crm act prep act! ad migration ada compliance ada guidelines adabas adb adb adapter adcs addie addm ade adea adfs adfs 2.0 adhd coaching adi adic adina adk adl adm adme admet adms ado.net adodb adp e-time adp hrb adp payforce adp payroll adp reportsmith adp ezlabormanager adr recording adrs ads-b adsi adso adt aduc adx ae aea aec aermod aes afaa afaa certified personal trainer afdx afe afis aflp afm afs aft fathom aftra agi 32 aha ahdl ahlta ahp ahu ahwd aia aia billing aia documents aiag aic aicc aicp aidc aiesec aif aiml aimsun aimsweb ain air air for android extension aisc aix 5.x aix administration ajax ajax frameworks ajax toolkit akta alarp alc alco ale alf alll alm alm/tfs alp alsa alta alta surveys alv alv reporting alv reports ama style amag amb amba amba ahb amc amcs amd64 amel amesim amfi amfi certified amfphp amhs ami aml amls amos ampl amps amqp amr amrt ams360 amsi property management amx amx programmer ancc anco

## Job Recommendations
Using cosine similarities of normalized tf-idf values, we can return the top 5 recommended jobs for each of the user profiles specified above.

In [13]:
def get_recommendations(input_skills_string):
    #cosine similarity
    current_item = jobs_rec_df.loc[input_skills_string].values.reshape(-1,1)
    similarities = jobs_rec_df.dot(current_item).reset_index()
    recommended_jobs = similarities.nlargest(n=6, columns=0)
    recommended_jobs = pd.merge(recommended_jobs.reset_index(), 
                                jobs_df, 
                                left_on="index", 
                                right_on="words")[["title","company","summary", 0, "link"]]
    recommended_jobs = recommended_jobs.rename(columns = {0: 'score'})
    return similarities, recommended_jobs
  
output_job_recommendations = [get_recommendations(input_skills_string) for input_skills_string in input_skills_strings]

In [14]:
def display_job_recomendations(user_output):
  similarities, recommended_jobs = user_output
  display(recommended_jobs[["title","company","summary", "score"]].sort_values('score', ascending = False).head(5))

### Data Analyst
Inputed Skills: "Python", "R", "SQL", "Tableau", "Power BI", "Salesforce", "Excel", "Machine Learning", "Statistics", "Analytics", "Visualization", "Web Scraping", "Bigquery".

In [16]:
display_job_recomendations(output_job_recommendations[0])

title company summary score Data Scientist TIAA Experience with Tableau or other BI/visualization tool. Research and application of technical methods to support diverse business needs.... 0.43081877976100186 CRM Measurement Analyst KOHLS Uses Machine Learning and data modeling to create business insights. Implements improvements through existing processes. Proficient with SQL and excel.... 0.3611972528767728 Data Scientist Kingswell Services Data Scientist – Machine Learning. Data Engineer with Data Architect background. Data Scientists – Machine Learning. Data Scientist of Machine Learning.... 0.35374360924208814 Statistical Data Analyst American Public Education Inc. Acquires data, which often will require SQL queries or publicly-available external data-sets, and makes logical conclusions about complex data to prepare it for... 0.3350564776804776 Global CRM Business Analyst Under Armour Experience with Customer Database reporting and Salesforce Marketing Cloud desired. Partner with team to identify tool and technology to improve analytical... 0.31478399693997194

### Software Engineering
Inputed Skills: "SQL", "Web Apps", "React", "Angular", "Full Stack", "JavaScript", "Node.js", "Python", "AWS", "Java", "C++", "NOSQL", "Graph Database", "Express", "Pyspark", "BigQuery", "S3", "Serverless", "Lambda"

In [18]:
display_job_recomendations(output_job_recommendations[1])

title company summary score Front-end Angular Developer Access One Deep hands-on experience in Javascript and Angular. Candidate must have understanding of user interfaces from a coding perspective.... 0.36982056618937076 Jr. Software Engineer Hatchways Full-time, Internship, Contract. Experience using AWS or Google Cloud Platform. Interest in scalable, efficient solutions and distributed systems.... 0.31762639389151237 Web UI Developer - NodeJS First Soft Solutions [ Direct] Solid knowledge of Node.js and frameworks like Express and Koa. Automated JavaScript testing frameworks (e.g. Please cut and paste job description here.... 0.3066521794777506 Angular Front End Developer STPT \*Experience working in an AWS environment moves you to the TOP of the list. If you have a passion for building stunning user interfaces that employ cutting... 0.30384359388760374 Angular Frontend Developer Layer 7 Data Solutions Job Title*:. Angular Frontend Developer. Total Estimated Assignment Hours:. 12 months.... 0.3034455988720181

### Data Engineer
Inputed Skills: "MapReduce", "Hadoop", "Data Mining", "ETL", "SPSS", "Java", "Scala", "SQL", "NOSQL", "Cloudera"

In [20]:
display_job_recomendations(output_job_recommendations[2])

title company summary score Big Data Architect Honeywell Experience with RESTful Web Service Design. 3+ years of experience working as a member of an Agile team. Review functional and technical requirements, raising... 0.25987606245241607 Data Scientist Source Enterprises Doing ad-hoc analysis and presenting results in a clear manner. Understanding of machine learning techniques and algorithms, such as:.... 0.2574703786112438 Junior Data Scientist SAIC Design and implement new analytics & dashboards. Analyzes, evaluates, and integrates data mining solutions to complex and diverse problem sets.... 0.2560344217575253 Systems Analyst Archbold Medical Center \*\*\*This is not a remote position; This position is located in Thomasville, GA.*. Troubleshoots, analyzes and solves complex problems, provides guidance and... 0.23834255729496684 Advanced Analytics Data Modeler Media Storm, LLC Extensive knowledge with machine learning, statistical models and data mining tools. 1-3 years of relevant hands-on work experience.... 0.2348619452377912

###Web Developer
Inputed Skills: "HTML", "CSS", "Javascript", "Ajax", "PHP", "ASP", "Java", "SEO", "SQL"

In [22]:
display_job_recomendations(output_job_recommendations[3])

title company summary score Intermediate/Junior Web Developer Social Concepts 1+ years hands-on experience with the following technologies:. PHP, AJAX, HTML/CSS, JavaScript, JQuery. In Computer Science or related discipline.... 0.48708856440874104 Junior Front End Developer (Contract to Hire) RG Barry Brands Our organization is looking for a Junior Front End Developer who can utilize HTML, CSS and JavaScript to develop effective user interfaces for our customer... 0.4467741136605145 Programmer/Database Administrator CMR & Associates Inc Must have a good understanding of front and back-end technologies, including HTML, CSS, JavaScript, jQuery. Strong understanding of PHP back-end development.... 0.42213123695724414 Frontend Developer booj We are looking for web developers with experience taking Photoshop designs and turning them into web ready products using LESS/CSS, HTML and JavaScript/jQuery.... 0.419449164823337 Web Developer University of Kentucky PHP, Javascript, SQL, HTML, CSS, UNIX, python. The software needed for this stage includes a map-based browsing interface that will allow visitors to browse the... 0.3934905502794318

###UI UX Designer
Inputed Skills: "Agile", "Prototyping", "Wireframing", "Design", "Data", "User Research", "Business"

In [24]:
display_job_recomendations(output_job_recommendations[4])

title company summary score UX Design Internship BB&T The following is a summary of the essential functions for this job. Solid skills in the use of one or more wireframing or prototyping tools.... 0.5414138627630477 UX/UI Designer RxSense Build Interactive Prototypes for proof of concepts. Working knowledge of Mobile UI/UX best practices and keeps up to date with modern schematics.... 0.4964900204528507 UX / UI Designer Curious Panda Group Hands-on experience in sketching solutions and wireframing. Communicate design concept ideas through sketches and wireframes.... 0.4120946386959713 Junior UX Designer TripleLift Forbes Most Promising Companies in America (Forbes - 2015). Startup of the Year Finalist (AdWeek - 2015). Crain's Best Places to Work - three years running!... 0.41128434749080606 UX Designer Peloton Coordinate, execute, and document user research. Evaluate, test, and iterate on current core experiences. Familiarity with agile software development and lean... 0.4024311406511464

###Game developer
"C++", "Visual Basic", "Java", "Autodesk Maya", "Physics", "Unity", "C#", "xcode", "Photoshop", "Autodesk 3dMax"

In [26]:
display_job_recomendations(output_job_recommendations[5])

title company summary score Customer Support and Operations Associate Autodesk Effective analytical and troubleshooting skills. Love to help / Go the extra mile:. Continually innovate and iterate on processes to maximize customer support... 0.5914716800635638 Game/Application Developer - Unity/Unreal GWF Associates, LLC We are a central NJ based multimedia development agency looking for a full-time Unity Developer to work on-site developing new applications and working on... 0.291720597524592 Xcode Debugger UI Engineer Apple Jun 26, 2019. Weekly Hours:. Role Number:. The Xcode team provides the tools to develop software for Apple's innovative iOS, watchOS, tvOS and macOS platforms.... 0.24482763210899136 Unity Developer New York Technology Partners Job Summary Hi Job Title: Unity Developer Location: San Francisco, CA Duration: 12+ Months Our client is looking for Unity developer, who has... 0.2351610769860508 Unity 3D Developers Designing Digitally Job Description :. Unity 3D Developers. Designing Digitally, Inc. Is looking for creative individuals who are familiar with working within Unity3D.... 0.22749417043475206

## Skill Recommendations
Now that we have job recommendations for each example user profile, we can also recommend additional skills for each profile. Using cosine similarities of the transposed `jobs_red_df` dataframe, we can see the similarity values between each skill.

In [28]:
skills_rec = cosine_similarity(jobs_rec_df.transpose(), jobs_rec_df.transpose())
skills_rec_df = pd.DataFrame(skills_rec, index = list(skills_df.name.values), columns = list(skills_df.name.values))
display(skills_rec_df.head())

(ISC)2 .NET .NET CLR .NET Compact Framework .NET Framework .NET Remoting .Net Core .com .htaccess 1-4 Units 1-Wire 1-to-1 Marketing 100% Financing 100-105 100D 1031 Exchanges 1099 Preparation 10G Ethernet 10K 10Q 10b5-1 Plans 10gR2 10gen 1120S 11781 11gR1 11gR2 123D Catch 123D Design 12c 12c Release 2 144A 16PF 1709 18th Century 1940 Act 19th Century 1H NMR 1Password 1SYNC 1ShoppingCart 2-D 2-D Design 20-20 CAP Studio 20/20 Design 20/20 Design Software 20/20 Technologies 200-101 2008 R2 2012 R2 2013 (Lync) 2014a 2015a 2016 R2 2017a 203K 20th Century 21 CFR 21st Century Skills 220-801 220-802 220-901 220-902 24 Hour Emergency Service 24x7 24x7 Production Support 27.x 2D Animation 2D CAD Drawing 2D Drawing 2D Software 2D art 2D graphics 2D to 3D Conversion 2Do 2G 2V0 2nd Line 2v0-641 2ε 340B 35mm 360 360 Assessments 360 Campaigns 360 Degree Assessment 360 Feedback 360 Recruitment 360s 365 37signals 3CX 3Com NBX 3Com Switches 3D + Animation 3D Animation 3D Architectural Rendering 3D Coat 3D Design 3D Drawing 3D GIS 3D Graphic Design 3D Graphics 3D Home Architect 3D Mapping 3D Materials 3D Math 3D Modeling 3D Modeling Software 3D Packaging 3D Particles and Dynamics 3D Printing 3D Production 3D Prototyping 3D Reconstruction 3D Rendering 3D Scanning 3D Secure 3D Seismic Interpretation 3D Simulation 3D Studio Max 3D Studio Viz 3D Textures 3D Tracking 3D Typography 3D Visualization 3D and Animation 3D displays 3D, Animation & CAO 3D, Animation und CAD 3D, animación y CAD 3D-Beleuchtung 3D-Druck 3D-Grafik 3D-Materialien 3D-Modellierung 3D-Partikel und Dynamik 3D-Texturen 3DCom 3DES 3DEqualizer 3DTV 3DVIA Composer 3Delight 3G 3GPP 3GPP2 3P 3PAR 3d 3ds Max 3rd Line Support 3rd Party Integrations 3rd Party Liaison 3rd Party Partnerships 3rd Party Relationships 3rd Party Software Integration 4 Disciplines of Execution 401(k) Retirement Savings Plans 401k Rollovers 403 b 404 Compliance 409A 40G 457 Plans 480interactive 49CFR 4G 4GL 4K 4PL 4th Dimension 4x4 5 Why 5.1 Mixing 501c3 504 Plans 529 Plans 55+ Communities 5500s 5D 5ESS 5S 5Y 60D 63 Licenses 6502 Assembly 650D 68HC11 68K 68k Assembly 6D 6S 7 QC Tools 700D 701 7D Mark II 8 Wastes 8-D 802.11a 802.11b 802.11g 802.11i 802.11n 802.15.4 802.16e 802.1ag 802.1d 802.1q 802.1x 8051 Assembly 8051 Microcontroller 80x86 837I 837P 89C51 8D Problem Solving 960 Grid System @Task Eclairage 3D Eclairage et rendu Eclairage photo Equipement photo Equipement video A + Certified A&D A&E A&H A&P A&R Administration A&U A+ A++ A-133 A-GPS A-frames A/B Testing A/R Collections A/R Management A/R analysis A1 Assessor A10 A2 A2A A3 A3 Thinking A320 A330 AAAHC AACR2 AAMS AAP AAR AASHTO AAUS Scientific Diver ABAP Web Dynpro ABAP-OO ABB 800xA ABBYY ABBYY FineReader ABC Analysis ABC Flowcharter ABCP ABEL ABI ABLS ABO Certified ABSYNTH ABV AC Drives AC Nielsen AC/DC ACAD ACARS ACATS ACBS ACD ACD Management ACDSee ACE ACE Certified ACE Certified Personal Trainer ACF2 ACFE ACH ACI Codes ACIS ACLS Instruction ACMS ACOA ACORD ACP ACPI ACR ACSA ACSC ACSLS ACSM ACSM Health Fitness ACSP ACSR ACSS ACT CRM ACT prep ACT! AD Migration ADA Compliance ADA guidelines ADABAS ADB ADB Adapter ADCs ADDIE ADDM ADE ADEA ADFS ADFS 2.0 ADHD Coaching ADI ADIC ADINA ADK ADL ADM ADME ADMET ADMS ADO.NET ADODB ADP E-Time ADP HRB ADP Payforce ADP Payroll ADP ReportSmith ADP ezLaborManager ADR Recording ADRs ADS-B ADSI ADSO ADT ADUC ADX AE AEA AEC AERMOD AES AFAA AFAA Certified Personal Trainer AFDX AFE AFIS AFLP AFM AFS AFT Fathom AFTRA AGI 32 AHA AHDL AHLTA AHP AHU AHWD AIA AIA Billing AIA Documents AIAG AIC AICC AICP AIDC AIESEC AIF AIML AIMSUN AIMSweb AIN AIR AIR for Android Extension AISC AIX 5.x AIX Administration AJAX AJAX Frameworks AJAX Toolkit AKTA ALARP ALC ALCO ALE ALF ALLL ALM ALM/TFS ALP ALSA ALTA ALTA Surveys ALV ALV Reporting ALV Reports AMA style AMAG AMB AMBA AMBA AHB AMC AMCs AMD64 AMEL AMESim AMFI AMFI Certified AMFPHP AMHS AMI AML AMLS AMOS AMPL AMPS AMQP AMR AMRT AMS360 AMSI Property Management AMX AMX Programmer ANCC ANCO

### Function to Return Recommendations
To use the skill cosine similarities to get recommendations, a custom `skill recommender` function is created. This function ensures that all the inputs in the user skills are in the skills dictionary (if not, that skill is not used for recommendations). The `is_word_in_phrase` function checks that skills that the user already knows are not recommended again. The final output of the code chunk below is a list of unique recommended skills for each user profile and the cosine similarity for each recommendation. The output is an aggregation of the best recommendations for each skill in each user's skillset. Finally, the `display_skill_recommendations` function displays these results for users.

In [30]:
def is_word_in_phrase(word, phrase):
  return word.lower() == phrase.lower()

def skill_recommender(skill_list, matrix, vocabulary):
    skill_recs_all = pd.Series()
    skill_scores_all = pd.Series()
    for skill in filter(lambda skill: skill in vocabulary, skill_list):
        result = matrix.sort_values(skill,ascending=False)
        skill_recs = pd.Series()
        skill_scores = pd.Series()
        max_recs = 5
        found = 0
        while found < max_recs:
          temp_rec = result[skill].index.values[i]
          if not is_word_in_phrase(skill, temp_rec):
            temp_score = round(result[skill][i],3)
            skill_recs = skill_recs.append(pd.Series(temp_rec))
            skill_scores = skill_scores.append(pd.Series(temp_score))
            found = found + 1
        skill_recs_all = skill_recs_all.append(skill_recs)
        skill_scores_all = skill_scores_all.append(skill_scores)
    skill_recommendations = pd.concat([skill_recs_all, skill_scores_all], axis=1, ignore_index=True)
    return skill_recommendations.drop_duplicates(subset=0).rename(columns={0: 'skill', 1: 'score'})
  
output_skill_recommendations = [skill_recommender(skills, skills_rec_df, skills_df['name'].values) for profile, skills in user_profiles]

def display_skill_recommendations(user_output):
  display(user_output[["skill","score"]].sort_values('score', ascending = False).head(10))

### Data Analyst
Inputed Skills: "Python", "R", "SQL", "Tableau", "Power BI", "Salesforce", "Excel", "Machine Learning", "Statistics", "Analytics", "Visualization", "Web Scraping", "Bigquery".

In [32]:
display_skill_recommendations(output_skill_recommendations[0])

skill score Python 0.337 Report Building 0.328 Java 0.325 Databases 0.324 Statisticians 0.319 Outlook 0.303 Visualization Software 0.295 Marketing Analytics 0.285 Soft Skills 0.28 Dashboards 0.276

### Software Engineering
Inputed Skills: "SQL", "Web Apps", "React", "Angular", "Full Stack", "JavaScript", "Node.js", "Python", "AWS", "Java", "C++", "NOSQL", "Graph Database", "Express", "Pyspark", "BigQuery", "S3", "Serverless", "Lambda"

In [34]:
display_skill_recommendations(output_skill_recommendations[1])

skill score Spring MVC 0.286 Python 0.263 PostGIS 0.254 Payment Services 0.0

### Data Engineer
Inputed Skills: "MapReduce", "Hadoop", "Data Mining", "ETL", "SPSS", "Java", "Scala", "SQL", "NOSQL", "Cloudera"

In [36]:
display_skill_recommendations(output_skill_recommendations[2])

skill score Databases 0.324 Preventive Medicine 0.322 Cloudera 0.311 Scala 0.304 Spring MVC 0.286 Data Warehouse 0.275

###Web Developer
Inputed Skills: "HTML", "CSS", "Javascript", "Ajax", "PHP", "ASP", "Java", "SEO", "SQL"

In [38]:
display_skill_recommendations(output_skill_recommendations[3])

skill score Web 0.442 Moz 0.419 JQuery 0.371 Databases 0.324 WordPress 0.29 Spring MVC 0.286

###UI UX Designer
Inputed Skills: "Agile", "Prototyping", "Wireframing", "Design", "Data", "User Research", "Business"

In [40]:
display_skill_recommendations(output_skill_recommendations[4])

skill score User Experience 0.397 Rapid Prototyping 0.373 UX 0.252 Testing 0.242

###Game developer
"C++", "Visual Basic", "Java", "Autodesk Maya", "Physics", "Unity", "C#", "xcode", "Photoshop", "Autodesk 3dMax"

In [42]:
display_skill_recommendations(output_skill_recommendations[5])

skill score JD Edwards 0.394 Havok 0.392 Character Animation 0.316 Spring MVC 0.286 Payment Services 0.0

## Conclusion

Using BigQuery, I was able to store large amounts of Indeed job listings and LinkedIn skills. The tf-idf method, cosine similarity, and job / skill recommendations were performed using PySpark. The recommendations for my user profile were helpful - I applied for several of my recommended jobs. I am also interested in many of the skills recommended for me, such as Java and Marketing Analytics. 

There were some questionable recommendations, such as 'Preventative Medicine' for Data Engineers, however it seems like all the User Profiles had at least a few relevant jobs and skills suggested.

In the future, I would like to add to this project to focus on other fields as well (not just tech). I also plan on creating a user interface that allows users to input their own skill profiles and view recommendations. Finally, I want to experiment with using word2vec rather than just tf-idf and compare quality of results.